In [1]:
import pandas as pd
from pathlib import Path
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
from statsmodels.tsa.arima.model import ARIMA
from fuzzywuzzy import fuzz, process
from itertools import combinations
import sys

sys.path.append('../Funciones')  # Aacceder a la carpeta Funciones
from funciones import graficar_interactivo
from funciones import nivel_socioeconomico_AMAI
from funciones import estadistica_descriptiva
from funciones import analizar_columnas
from funciones import gastohogar_zona_estudio
from funciones import obtener_claves_estado_mun
from funciones import NSE_CONEVAL

# Bibliografica fecha de consulta 05/febrero/2025
#https://www.coneval.org.mx/Medicion/MP/Paginas/Programas_BD_2022.aspx

c:\Users\julio_2h7cnt5\AppData\Local\Programs\Python\Python313\Lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [ ]:
# Ruta relativa al archivo CSV
csv_path = Path("..") / "MacroDatos" / "PIB_Historico.csv"

# Ruta relativa al archivo CSV
csv_pobreza = Path("..") / "MacroDatos" / "pobreza22.csv"

# Ruta relativa al archivo CSV
nse_amai = Path("..") / "MacroDatos" / "NSE_por_AGEB_AMAI.xlsx"

# Ruta relativa al archivo CSV
nuclear = Path("..") / "Proyecto Pinsa" / "Nuclear.xlsx"

# Ruta relativa al archivo CSV
extendido = Path("..") / "Proyecto Pinsa" / "Extendido.xlsx"

# Ruta relativa al archivo CSV
consentradohogar = Path("C:/Users/julio_2h7cnt5/OneDrive/Documentos/Ideas Frescas/MacroDatos/enig_concentradohogar.csv") 



In [ ]:
# Lee el archivo CSV
pib = pd.read_csv(csv_path,on_bad_lines='skip') # PIB México

pobreza_data = pd.read_csv(csv_pobreza) # Base de datos CONEVAL

extendido = pd.read_excel("Extendido.xlsx") # Zona extendida

nuclear = pd.read_excel("Nuclear.xlsx") # Zona Nuclear

PIB por estado y sus variaciones 

In [ ]:
pib = pib.drop([0,1,3])
pib_total = pib.iloc[2:34]
pib_porcentaje = pib.iloc[38:70]
pib_volumen_fisico = pib.iloc[74:106]
pib_variacion_anual = pib.iloc[110:142]
pib_conribucion_variacion_nacional = pib.iloc[146:178]
pib_participacion_porcentual = pib.iloc[219:251]

In [ ]:
''' 
# Transformar el DataFrame
df_melted = pib_total.melt(id_vars=['Concepto'], var_name='Año', value_name='PIB')

# Verificar si hay valores no numéricos en la columna 'PIB'
print(df_melted['PIB'].apply(type).value_counts())

# Convertir la columna 'PIB' a tipo numérico (float)
df_melted['PIB'] = pd.to_numeric(df_melted['PIB'], errors='coerce')

# Verificar si hay valores nulos después de la conversión
print(df_melted['PIB'].isnull().sum())

'''

Ingresos México

    - Diccionario de datos

In [ ]:
# VARIABLES
'''
1 folioviv: Identificador de la vivienda
2 foliohog: Identificador del hogar
3 numren: Identificador de la persona
4 est_dis: Estrato de diseño
5 upm: Unidad primaria de muestreo
6 factor: Factor de expansión
7 tam_loc: Tamaño de la localidad (de acuerdo con el descriptor de la base de la ENIGH 2022 del INEGI)
8 rururb: Identificador de localidades rurales
9 ent: Identificador de la entidad federativa
10 ubica_geo: Ubicación geográfica
11 edad: Edad reportada al momento de la entrevista
12 sexo: Sexo (de acuerdo con el descriptor de la base de la ENIGH 2022 del INEGI)
13 parentesco: Parentesco con el jefe del hogar (consultar catálogo del INEGI)
14 ic_rezedu: Indicador de rezago educativo
15 anac_e: Año de nacimiento
16 inas_esc: Inasistencia a la escuela
17 niv_ed: Nivel educativo
18 ic_asalud: Indicador de carencia por acceso a servicios de salud
19 ic_segsoc: Indicador de carencia por acceso a la seguridad social
20 sa_dir: Acceso directo a servicios de salud
21 ss_dir: Acceso directo a la seguridad social
22 s_salud: Servicios médicos por otros núcleos familiares o por contratación propia
23 par: Integrantes que tienen acceso por otros miembros
24 jef_ss: Acceso directo a la seguridad social de la jefatura del hogar
25 cony_ss: Acceso directo a la seguridad social de cónyuge de la jefatura del hogar
26 hijo_ss: Acceso directo a la seguridad social de hijos(as) de la jefatura del hogar
27 pea: Población económicamente activa
28 jub: Población pensionada o jubilada 
29 pam: Programa de adultos mayores
    0. No recibe
    1. Recibe
30 ing_pam: Ingreso promedio mensual por programas de adultos mayores
31 ic_cv: Indicador de carencia por calidad y espacios de la vivienda
    0. No presenta carencia
    1. Presenta carencia
32 icv_pisos: Indicador de carencia por material de piso de la vivienda
    0. No presenta carencia
    1. Presenta carencia
33 icv_muros: Indicador de carencia por material de muros de la vivienda
    0. No presenta carencia
    1. Presenta carencia
34 icv_techos: Indicador de carencia por material de techos de la vivienda
    0. No presenta carencia
    1. Presenta carencia
35 icv_hac: Indicador de carencia por hacinamiento en la vivienda
    0. No presenta carencia
    1. Presenta carencia
36 ic_sbv: Indicador de carencia por acceso a servicios básicos en la vivienda
    0. No presenta carencia
    1. Presenta carencia
37 isb_agua Indicador de carencia por acceso al agua
    0. No presenta carencia
    1. Presenta carencia
38 isb_dren: Indicador de carencia por servicio de drenaje
    0. No presenta carencia
    1. Presenta carencia
39 isb_luz: Indicador de carencia por servicios de electricidad
    0. No presenta carencia
    1. Presenta carencia
40 isb_combus: Indicador de carencia por combustible para cocinar
    0. No presenta carencia
    1. Presenta carencia
41 ic_ali_nc: Indicador de carencia por acceso a la alimentación nutritiva y de calidad
    0. No presenta carencia
    1. Presenta carencia
42 id_men: Hogares con población de 0 a 17 años
    0. Sin población de 0 a 17 años
    1. Con población de 0 a 17 años
43 tot_iaad: Escala de IA para hogares sin menores de 18 años
44 tot_iamen: Escala de IA para hogares con menores de 18 años
45 ins_ali: Grado de Inseguridad Alimentaria
    0. Seguridad alimentaria
    1. Inseguridad alimentaria leve
    2. Inseguridad alimentaria moderada
    3. Inseguridad alimentaria severa
46 ic_ali: Indicador de carencia por acceso a la alimentación
    0. No presenta carencia
    1. Presenta carencia
47 lca: Limitación en el consumo de alimentos
    0. No limitado
    1. Limitado
48 dch: Dieta consumida en los hogares
    1. Pobre
    2. Limítrofe
    3. Aceptable
49 plp_e: Población con ingreso menor a la línea de pobreza extrema por ingresos
    0. Ingreso superior o igual a la línea de pobreza extrema por ingresos
    1. Ingreso inferior a la línea de pobreza extrema por ingresos
50 plp: Población con ingreso menor a la línea de pobreza por ingresos
    0. Ingreso superior o igual a la línea de pobreza por ingresos
    1. Ingreso inferior a la línea de pobreza por ingresos
51 pobreza: Pobreza
    0. No pobre
    1. Pobre
52 pobreza_e: Pobreza extrem
    0. No pobre extremo
    1. Pobre extremo
53 pobreza_m: Pobreza moderada
    0. No pobre moderado
    1. Pobre moderado
54 vul_car:  Población vulnerable por carencias
    0. No vulnerable
    1. Vulnerable
55 vul_ing:  Población vulnerable por ingresos
    0. No vulnerable
    1. Vulnerable
56 no_pobv: Población no pobre y no vulnerable
    0. Pobre o vulnerable
    1. No pobre y no vulnerable
57 i_privacion: Índice de Privación Social
58 carencias: Población con al menos una carencia social
    0. Población sin carencias sociales
    1. Población con al menos una carencia social
59 carencias3: Población con al menos tres carencias sociales
    0. Población con menos de tres carencias sociales
    1. Población con al menos tres carencias sociales
60 cuadrantes: Cuadrantes de bienestar económico y derechos sociales
    1. Pobres
    2. Vulnerables por carencias
    3. Vulnerables por ingresos
    4. No pobres y no vulnerables
61 prof1: Índice FGT con alfa igual a 1 (línea de pobreza por ingresos)
62 prof_e1: Índice FGT con alfa igual a 1 (línea de pobreza extrema por ingresos)
63 profun: Profundidad de la privación social
64 int_pob: Intensidad de la privación social: en situación de pobreza
65 int_pobe:  Intensidad de la privación social: en situación de pobreza extrema
66 int_vulcar: Intensidad de la privación social: población vulnerable por carencias
67 int_caren: Intensidad de la privación social: población con carencias sociales
68 tamhogesc: Tamaño del hogar ajustado
69 ictpc: Ingreso corriente total per cápita
70 ict: Ingreso corriente total del hogar
71 ing_mon: Ingreso corriente monetario del hogar
72 ing_lab: Ingreso corriente monetario laboral
73 ing_ren: Ingreso corriente monetario por rentas
74 ing_tra: Ingreso corriente monetario por transferencias
75 nomon: Ingreso corriente no monetario
76 pago_esp: Ingreso corriente no monetario pago especie
77 reg_esp: Ingreso corriente no monetario regalos especie
78 hli: Hablante de lengua indígena
    0. No habla lengua indígena
    1. Habla lengua indígena
79 discap: Población con presencia de discapacidad física o mental
    0. Sin presencia de discapacidad
    1. Con presencia de discapacidad

'''   
# Entidad Federativa
'''
Identificar la entidad federativa. 
    1: 'Aguascalientes',
    2: 'Baja California',
    3: 'Baja California Sur',
    4: 'Campeche',
    5: 'Coahuila',
    6: 'Colima',
    7: 'Chiapas',
    8: 'Chihuahua',
    9: 'Ciudad de México',
    10: 'Durango',
    11: 'Guanajuato',
    12: 'Guerrero',
    13: 'Hidalgo',
    14: 'Jalisco',
    15: 'México',
    16: 'Michoacán',
    17: 'Morelos',
    18: 'Nayarit',
    19: 'Nuevo León',
    20: 'Oaxaca',
    21: 'Puebla',
    22: 'Querétaro',
    23: 'Quintana Roo',
    24: 'San Luis Potosí',
    25: 'Sinaloa',
    26: 'Sonora',
    27: 'Tabasco',
    28: 'Tamaulipas',
    29: 'Tlaxcala',
    30: 'Veracruz',
    31: 'Yucatán',
    32: 'Zacatecas'    
'''

Clasificar el Nivel Socioeconomico Mazatlán

In [ ]:
# 3. Sinaloa Mazatlán
resultados_maza = NSE_CONEVAL(estado=25, municipio=25012)
resultados_maza

In [ ]:
# Paleta de colores
pastel_colors = ['#FFB3BA', '#FFDFBA', '#FFFFBA', '#BAFFC9', '#BAE1FF', '#D9D9D9', '#FFB3D9']

# Crear la gráfica de barras interactiva con Plotly
fig = px.bar(resultados_maza, x='Nivel Socioeconomico', y='Ingreso Promedio', 
             text='Ingreso Promedio', labels={'Ingreso Promedio ': 'Ingreso Promedio '},
             title='Ingreso Promedio por Nivel Socioeconómico', color='Nivel Socioeconomico',
             color_discrete_map={label: pastel_colors[i] for i, label in enumerate(labels)})

# Mejorar la presentación del texto en las barras
fig.update_traces(texttemplate='%{y:.2f}', textposition='outside')  # Cambié 'inside' por 'outside'

# Añadir una línea horizontal roja punteada para el promedio general
fig.add_trace(go.Scatter(
    x=resultados_maza['Nivel Socioeconomico'],
    y=[promedio_general] * len(resultados_maza),
    mode='lines',
    text=[f'{promedio_general:.2f}'] * len(resultados_maza),
    line=dict(color='red', dash='dot'),
    name='Promedio Genearal'
))

# Ajustar la posición de la leyenda
fig.update_layout(legend=dict(
    orientation="h",  # Leyenda horizontal
    yanchor="bottom", # Anclada en la parte inferior
    y=-0.3,           # Posición fuera del gráfico
    xanchor="right",  # Anclada a la derecha
    x=1               # Posición a la derecha
))

# Mostrar la gráfica
fig.show()

Descripcion estadistica del salario en Mazatlán

In [ ]:
estadistica_descriptiva(pobreza_data,'ictpc')

Clasificar el Nivel Socioeconomico México

In [ ]:
# Obtener 'CVE_ENT' y 'CVE_MUN' para Sinaloa y Mazatlán
claves= obtener_claves_estado_mun('Baja California Sur', 'Los Cabos')
print(f"Claves para Sinaloa, Mazatlán: {claves}")

In [ ]:
# NSE a Nivel Nacional
resultados_todos = NSE_CONEVAL()
resultados_todos


In [3]:
# NSE Nivel Sinaloa 
resultados_sinaloa = NSE_CONEVAL(estado=25)
resultados_sinaloa 

Nivel Socioeconomico  Ingreso Promedio  Porcentaje
0                    E           2824.00   47.245549
1                    D           6001.05   31.012765
2                   D+          12044.37   17.408465
3                   C-          22102.70    3.359086
4                    C          36958.92    0.697010
5                   C+          62907.86    0.251931
6                  A/B         684060.04    0.025193

In [2]:
# NSE Nivel Baja California Sur
resultados_BCS = NSE_CONEVAL(estado=3)
resultados_BCS 

Nivel Socioeconomico  Ingreso Promedio  Porcentaje
0                    E           2792.63   46.830944
1                    D           6230.73   23.492477
2                   D+          12391.81   20.767682
3                   C-          22664.77    6.006397
4                    C          35700.62    1.765194
5                   C+          61090.58    0.912214
6                  A/B         151695.49    0.225092

In [ ]:
# 3. Baja California Sur  Los Cabos
resultados_cabo = NSE_CONEVAL(estado=3, municipio=3008)
resultados_cabo

NSE por AGEB por el AMAI para Mazatlán: Proyecto PINSA

In [ ]:
# Filtrar por AGEB y Manzana 
# Concatenar y filtrar zona_total_estudio
# Concatenar los DataFrames y seleccionar solo la columna 'CVE_AGEB', luego convertir los valores únicos a texto
zona_total_estudio  = pd.concat([extendido, nuclear], ignore_index=True)['CVE_AGEB'].astype(str).unique().tolist()


In [ ]:
nivel_socioeconomico_AMAI('Sinaloa','Mazatlán',zona_total_estudio )

GASTO POR HOGAR NIVEL NACIONAL

In [ ]:
'''
Como se conforma el folioviv
"01-034-001-002-000"

    01: Aguascalientes (estado)
    034: Municipio de Aguascalientes (municipio)
    001: Localidad (una zona en el municipio)
    002: Manzana (una subdivisión dentro de la localidad)
    000: Número de orden de vivienda

El diccionario para el codigo de los productos que en lo que gastan los hogares son los siguientes si:

Alimentos: 'A', T901

Limpieza: 'C', T903

Personales: 'D', F002,R007,L029,N001, N002, N012, N013, N014, N015,T904

Educación: 'E', T905

Transporte: 'B','M', F001, F003, F004, F005, F006, F007, F008, F009, F010, F011, F012, F013, F014, R005, R006, R012, L013 N008, N016 T902, T914, T906

Vivienda: 'G','I','K' R001, R002, R003, R004, R008, R009, R010, R011, R013, N005, N007, N009, T907, T910, T912

Vestido y Calzado, 'H', T909

Salud: 'J', T911

Esparcimiento: L001, L002, L003, L004, L005, L006, L007, L008, L009, L010, L011, L012, L014, L015, L017, L018, L019, L020, L021, L022, L023, L024, L025, L026, L027, L028, N003, N006, T913

Turísticos N004

Transparencias de Gasto: N010, N011, T908, T915, T916
'''

In [ ]:
# Llamada a la función para filtrar y clasificar los datos
estado = '25'
municipio = '026'
localidad = '076'
gastohogar_resultado = gastohogar_zona_estudio(estado, municipio, localidad)

# Ver el resultado
gastohogar_resultado

In [ ]:
gastohogar_resultado['folioviv'].value_counts()

In [ ]:
diccigast_data = pd.read_csv("C:/Users/julio_2h7cnt5/OneDrive/Documentos/Ideas Frescas/MacroDatos/diccionario_enigh_gastos.csv", encoding='ISO-8859-1')

# Diccionario para la columna de clave de cual es el gasto
diccigast = pd.Series(diccigast_data.iloc[:, 1].values, index=diccigast_data.iloc[:, 0].values).to_dict()

dict_tipo_gasto = {
    'G1': 'Gasto monetario en bienes y servicios para el hogar',
    'G2': 'Gasto monetario en bienes y servicios para otro hogar',
    'G3': 'Gasto no monetario procedente de autoconsumo',
    'G5': 'Gasto no monetario por regalos recibidos de otro hogar',
    'G6': 'Gasto no monetario por transferencias de instituciones',
    'G7': 'Gasto imputado por estimación del alquiler'}

dict_forma_pago = {
    0: 'No aplica',
    1: 'Efectivo',
    2: 'Fiado (persona particular o establecimiento comercial)',
    3: 'Domiciliación',
    4: 'Transferencia electrónica de fondos',
    5: 'Tarjeta de crédito',
    6: 'Tarjeta de débito',
    7: 'Cheque',
    8: 'Vale',
    9: 'Pago móvil',
    10: 'Otro'
}

# Crear el diccionario
dict_lugar_comp = {
    0: 'No aplica',
    1: 'Mercado',
    2: 'Tianguis o mercado sobre ruedas',
    3: 'Vendedores ambulantes',
    4: 'Tiendas de abarrotes',
    5: 'Tiendas específicas del ramo',
    6: 'Supermercados',
    7: 'Tiendas departamentales',
    8: 'Compras fuera del país',
    9: 'Tiendas con membresía',
    10: 'Tiendas de conveniencia',
    11: 'Restaurantes',
    12: 'Loncherías, fondas, torterías, cocinas económicas, cenadurías',
    13: 'Cafeterías',
    14: 'Pulquería, cantina o bar',
    15: 'Diconsa',
    16: 'Lechería Linconsa',
    17: 'Persona particular',
    18: 'Internet'
}

# Crear el diccionario
dict_frecuencia = {
    0: 'No aplica',
    1: 'Diario',
    2: 'Cada Semana',
    3: 'Una vez al mes',
    4: 'Cada año',
    5: 'Lo recibió una sola vez',
    6: 'Otros'
}


In [ ]:
clasificacion_gasto = analizar_columnas(gastohogar_resultado,'Clasificación gasto',100)
clasificacion_gasto


In [ ]:
productos = analizar_columnas(gastohogar_resultado,'clave',100).head(5)

# Seleccionar una fila del DataFrame (por ejemplo, la primera fila)
fila = productos.iloc[0]  # Seleccionar la primera fila (índice 0)

# Obtener la clave de la fila
clave_fila = fila['clave']

# Buscar la descripción en el diccionario usando la clave
descripcion = diccigast.get(clave_fila, "Clave no encontrada")

print(f"La descripción de la fila seleccionada ({clave_fila}) es: {descripcion}")
productos

In [ ]:
tipos_de_gasto = analizar_columnas(gastohogar_resultado,'tipo_gasto',100).head(5)
# Seleccionar una fila del DataFrame (por ejemplo, la primera fila)
fila = tipos_de_gasto.iloc[0]  # Seleccionar la primera fila (índice 0)

# Obtener la clave de la fila
clave_fila = fila['tipo_gasto']

# Buscar la descripción en el diccionario usando la clave
descripcion = dict_tipo_gasto.get(clave_fila, "Clave no encontrada")

print(f"La descripción de la fila seleccionada ({clave_fila}) es: {descripcion}")
tipos_de_gasto

In [ ]:
forma_pago = analizar_columnas(gastohogar_resultado,'forma_pag1',100).head(5)
# Seleccionar una fila del DataFrame (por ejemplo, la primera fila)
fila = forma_pago.iloc[2]  # Seleccionar la primera fila (índice 0)

# Obtener la clave de la fila
clave_fila = fila['forma_pag1']

# Buscar la descripción en el diccionario usando la clave
descripcion = dict_forma_pago.get(clave_fila, "Clave no encontrada")

print(f"La descripción de la fila seleccionada ({clave_fila}) es: {descripcion}")
forma_pago

In [ ]:
frecu = analizar_columnas(gastohogar_resultado,'frecuencia',100).head(5)
# Seleccionar una fila del DataFrame (por ejemplo, la primera fila)
fila = frecu.iloc[3]  # Seleccionar la primera fila (índice 0)

# Obtener la clave de la fila
clave_fila = fila['frecuencia']

# Buscar la descripción en el diccionario usando la clave
descripcion = dict_frecuencia.get(clave_fila, "Clave no encontrada")

print(f"La descripción de la fila seleccionada ({clave_fila}) es: {descripcion}")
frecu

In [ ]:
consentradohogar = pd.read_csv(consentradohogar)

In [ ]:
consentradohogar[consentradohogar['folioviv'].isin([2502607605, 2502607602,2502607601,2502607606,
                                                2502607604,2502607603])]